In [11]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

# Imports
import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

# Our application logic will be added here
def cnn_model_fn(features, labels, mode):
    #convert the features (28 x 28 x 1) into a 4D tensor - [batch size, height, widht, channel]
    input_layer = tf.reshape(features["x"],shape=[-1,28,28,1])
    #conv1
    conv1 = tf.layers.conv2d(
                            inputs = input_layer,
                            filters=32,
                            kernel_size = [5,5],        
                            padding="same",
                            activation = tf.nn.relu,
                            name = "conv1"
                            ) 
    
    #pool1
    pool1 = tf.layers.max_pooling2d(
                            inputs = conv1,
                            pool_size = [2,2],
                            strides = 2,
                            name = "pool1"
                            )
    
    #conv2
    conv2 = tf.layers.conv2d(
                            inputs = pool1,
                            filters=64,
                            kernel_size = [5,5],        
                            padding="same",
                            activation = tf.nn.relu,
                            name = "conv2"
                            )
    
    #pool2
    pool2 = tf.layers.max_pooling2d(
                            inputs = conv2,
                            pool_size = [2,2],
                            strides = 2,
                            name = "pool2"
                            )
    
    #flat pool output
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
    
    #dense
    dense1 = tf.layers.dense(
                            inputs = pool2_flat,
                            units = 1024,
                            activation = tf.nn.relu
                            )
    
    #drop out regularization
    
    dropout = tf.layers.dropout(
                                inputs = dense1,
                                rate = 0.4,
                                training = mode == tf.estimator.ModeKeys.TRAIN
                                )
    
    #dense
    logits = tf.layers.dense(inputs = dropout, units = 10)
    
    #softmax
    predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }

    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)
    
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)
    
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
                                       loss = loss,
                                       global_step = tf.train.get_global_step()
                                     )
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)
    
    eval_metric_ops = {
                        "accuracy" : tf.metrics.accuracy(labels=labels, predictions=predictions["classes"])
                      }
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

#def main(unused_argv):
   
mnist = tf.contrib.learn.datasets.load_dataset("mnist")
train_data = mnist.train.images
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
eval_data = mnist.test.images
eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)
    
mnist_classifier = tf.estimator.Estimator(model_fn = cnn_model_fn)
    
tensors_to_log = {"probabilities" : "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(tensors = tensors_to_log, every_n_iter =50)
    
train_input_fn = tf.estimator.inputs.numpy_input_fn(
                                                      x = {"x" : train_data},
                                                      y = train_labels,
                                                      batch_size = 100,
                                                      num_epochs = None,
                                                      shuffle = True
                                                    )
    
mnist_classifier.train(
                            input_fn = train_input_fn,
                            steps = 20000,
                            hooks = [logging_hook]
                          )
    
eval_input_fn = tf.estimator.inputs.numpy_input_fn(
                                                        x = {"x" : eval_data},
                                                        y = eval_labels,
                                                        num_epochs = 1,
                                                        shuffle = False
                                                      )
    
eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
print("Printing eval results")
print(eval_results)    
#if __name__ == "__main__":
#  tf.app.run()


Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/tmpb1op5mth', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7ff3e3cf37b8>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Run

INFO:tensorflow:loss = 2.2994297, step = 0
INFO:tensorflow:probabilities = [[0.11258592 0.07858323 0.10064092 0.09141617 0.08625618 0.08899686
  0.10668059 0.12096582 0.09824663 0.1156276 ]
 [0.10608722 0.08277623 0.09673922 0.09274965 0.10195027 0.10118371
  0.10614696 0.10103412 0.10016038 0.11117229]
 [0.10764843 0.08132987 0.09592706 0.11149828 0.09704463 0.10260789
  0.09906273 0.10540845 0.10697749 0.09249522]
 [0.09263234 0.10050644 0.09260415 0.0966586  0.09186463 0.10321186
  0.09818957 0.10031701 0.12235096 0.10166443]
 [0.11666384 0.07558957 0.10203397 0.11537263 0.0913084  0.09183001
  0.09055237 0.1155201  0.1081437  0.09298543]
 [0.10847498 0.08155727 0.09435699 0.10470697 0.09381346 0.09882312
  0.10134846 0.10923757 0.11070012 0.09698103]
 [0.12362128 0.08460475 0.10244986 0.07765541 0.09109973 0.11170698
  0.10524476 0.09953    0.1099413  0.09414595]
 [0.10067428 0.09659184 0.09690055 0.0959002  0.08687586 0.09799036
  0.09445097 0.107393   0.116263   0.10695997]
 [0.1

INFO:tensorflow:global_step/sec: 159.131
INFO:tensorflow:probabilities = [[0.1280817  0.07792678 0.09912714 0.08992662 0.0944837  0.09694099
  0.09272089 0.09499667 0.12471364 0.10108186]
 [0.10404202 0.09330349 0.10391085 0.09701303 0.10012951 0.09742051
  0.10080966 0.10216708 0.10049824 0.10070556]
 [0.11291324 0.08289022 0.09080013 0.09762209 0.09497237 0.09882265
  0.10066124 0.11729668 0.09885586 0.10516544]
 [0.11158194 0.08246341 0.09843775 0.10255551 0.10505623 0.09554281
  0.0929063  0.11719608 0.0984226  0.09583738]
 [0.10443737 0.08166735 0.10898941 0.08590657 0.10253265 0.09168956
  0.10549873 0.10859656 0.12067949 0.09000226]
 [0.11375    0.09280263 0.09545295 0.09625252 0.09028421 0.0942643
  0.10403867 0.10516687 0.11060788 0.09737998]
 [0.10756575 0.08903093 0.0947559  0.08941397 0.10082193 0.09947
  0.10778081 0.0990948  0.10219444 0.10987145]
 [0.12994939 0.07645418 0.10045253 0.08935557 0.09304567 0.08030494
  0.11702266 0.10551725 0.11140147 0.09649634]
 [0.1071815

INFO:tensorflow:loss = 2.2738357, step = 100 (0.631 sec)
INFO:tensorflow:probabilities = [[0.09925912 0.09395616 0.09218314 0.10176059 0.09949386 0.09220289
  0.09223585 0.10953315 0.10618433 0.11319087]
 [0.10504477 0.09602313 0.11132536 0.08774011 0.09391505 0.10158172
  0.09818844 0.09520084 0.10982008 0.10116052]
 [0.09950245 0.08004814 0.10242444 0.10166188 0.09670776 0.09892956
  0.10075594 0.10923389 0.11522672 0.09550928]
 [0.12052861 0.08053827 0.09191737 0.10711341 0.10259677 0.09113596
  0.1085924  0.09663835 0.09424002 0.10669889]
 [0.10014173 0.0831517  0.11149239 0.10278642 0.09472301 0.09539483
  0.11039168 0.10462797 0.09969833 0.09759197]
 [0.10594454 0.09315097 0.09625673 0.09442674 0.10448699 0.08668208
  0.09880402 0.10476328 0.10147996 0.1140047 ]
 [0.11007602 0.08420591 0.10018886 0.09893607 0.08519679 0.09298617
  0.10934772 0.10222524 0.10929474 0.10754247]
 [0.10435806 0.09363275 0.0950212  0.09723565 0.09876452 0.09713939
  0.09717768 0.10668006 0.10512335 0.1

INFO:tensorflow:global_step/sec: 208.601
INFO:tensorflow:probabilities = [[0.11351325 0.08151691 0.10332128 0.10106938 0.09447996 0.09152387
  0.10178027 0.0988238  0.11433808 0.09963317]
 [0.12583077 0.09466947 0.09515672 0.08694119 0.09098531 0.0879573
  0.10105868 0.10006823 0.11408333 0.10324901]
 [0.10304275 0.09479119 0.10089881 0.09697996 0.08901478 0.1014796
  0.10121114 0.10309844 0.10912366 0.1003597 ]
 [0.10612486 0.08146665 0.09250516 0.10299649 0.1003644  0.09312458
  0.10069445 0.10906283 0.09569351 0.11796705]
 [0.11059264 0.0934132  0.09723438 0.10253087 0.0953197  0.09099326
  0.09836797 0.10022211 0.12162369 0.08970224]
 [0.10906845 0.08075804 0.10225412 0.08494524 0.09369815 0.09784013
  0.11082675 0.11113907 0.10787964 0.10159036]
 [0.09694133 0.09636699 0.10947248 0.09357252 0.0901572  0.09053983
  0.1021118  0.09885138 0.11498968 0.1069968 ]
 [0.10359498 0.09061369 0.10736784 0.09423796 0.09634433 0.09238485
  0.09283876 0.11529158 0.10289177 0.10443421]
 [0.11160

...

INFO:tensorflow:global_step/sec: 221.207
INFO:tensorflow:probabilities = [[0.08828541 0.00310268 0.5199383  0.01237495 0.06707093 0.16002633
  0.10734673 0.0170433  0.02156318 0.00324823]
 [0.00000465 0.00000195 0.00006001 0.0000038  0.00010091 0.0000128
  0.9998079  0.00000001 0.000008   0.00000003]
 [0.00000692 0.00005793 0.00161554 0.00001951 0.9952779  0.00012313
  0.00272128 0.00001371 0.00011307 0.00005098]
 [0.00074037 0.0000451  0.0003074  0.09824012 0.00005253 0.8617704
  0.03749693 0.00000549 0.00110326 0.0002385 ]
 [0.00000847 0.9968156  0.00037062 0.00003304 0.00000866 0.00002166
  0.00002058 0.00012297 0.00255991 0.00003854]
 [0.00000007 0.00000696 0.9997539  0.00003662 0.00000329 0.00000016
  0.00000041 0.00019427 0.00000428 0.00000003]
 [0.00003396 0.00000443 0.00195113 0.00000147 0.01307388 0.00002628
  0.9847617  0.00000012 0.00001306 0.00013388]
 [0.00012625 0.00013397 0.00136679 0.0069496  0.50131226 0.14314893
  0.00148741 0.26874286 0.03069444 0.04603752]
 [0.00041

INFO:tensorflow:loss = 0.14291313, step = 19800 (0.454 sec)
INFO:tensorflow:probabilities = [[0.00007968 0.00007504 0.01113405 0.00126433 0.00000032 0.00005715
  0.00000005 0.97395873 0.00019628 0.01323434]
 [0.00044936 0.00000028 0.00002634 0.00025344 0.0000945  0.00083674
  0.00000055 0.9398789  0.00006112 0.05839874]
 [0.00380514 0.00002016 0.00016619 0.00002619 0.00056504 0.00160205
  0.990516   0.00000116 0.00328787 0.00001018]
 [0.00003226 0.00018266 0.0006903  0.9792853  0.00000061 0.01940888
  0.00000036 0.00002286 0.00030734 0.00006939]
 [0.00002536 0.00000144 0.00004659 0.00000197 0.00054515 0.00048037
  0.9988758  0.00000008 0.00002177 0.00000149]
 [0.00000004 0.00004602 0.9975478  0.00232617 0.00000002 0.00002958
  0.00000006 0.00000007 0.00005004 0.00000025]
 [0.00000862 0.00000024 0.0000587  0.00000007 0.00010707 0.00076012
  0.9990646  0.         0.0000004  0.00000014]
 [0.00025691 0.00101225 0.0004846  0.00482863 0.00170511 0.9890036
  0.00082275 0.0003775  0.00112709 0

INFO:tensorflow:global_step/sec: 213.628
INFO:tensorflow:probabilities = [[0.9999391  0.00000008 0.00002845 0.00000078 0.00000001 0.00001947
  0.00000394 0.00000034 0.00000026 0.00000761]
 [0.00013768 0.9952874  0.00108465 0.0000769  0.00002872 0.00001307
  0.00021628 0.0002913  0.00282962 0.00003435]
 [0.00000072 0.00000002 0.00000051 0.00027103 0.00014203 0.00006271
  0.00000001 0.00047239 0.00101971 0.99803084]
 [0.00125315 0.08632756 0.00364947 0.02673579 0.00457497 0.01692231
  0.7908592  0.00005678 0.06951089 0.00010985]
 [0.00001393 0.99259746 0.00007576 0.0001597  0.00010383 0.00008077
  0.00010293 0.00023698 0.00649804 0.00013047]
 [0.00001328 0.00000082 0.0001474  0.00030987 0.00000031 0.00000168
  0.00000001 0.99911875 0.00000084 0.00040694]
 [0.9996922  0.00000003 0.00023388 0.00000413 0.00000023 0.00001208
  0.00000264 0.00000817 0.0000055  0.00004127]
 [0.00000208 0.99975413 0.00001605 0.00000629 0.00001259 0.00000182
  0.00003067 0.00004523 0.00012875 0.00000245]
 [0.000

INFO:tensorflow:loss = 0.11716727, step = 19900 (0.469 sec)
INFO:tensorflow:probabilities = [[0.00033642 0.0075416  0.00053823 0.00156056 0.00110723 0.9802911
  0.00072833 0.00053983 0.00702022 0.00033646]
 [0.37975523 0.00044685 0.01626004 0.0009113  0.03016768 0.0007233
  0.00103191 0.30148447 0.01012468 0.25909448]
 [0.999534   0.00001016 0.00002619 0.00000538 0.00000027 0.00015173
  0.00026538 0.00000497 0.00000182 0.00000014]
 [0.00005448 0.00000018 0.00000006 0.00000291 0.00000193 0.00000295
  0.         0.99918336 0.00000004 0.00075411]
 [0.00583879 0.00002789 0.01069705 0.00243684 0.00525777 0.02963263
  0.0147379  0.00000291 0.9248174  0.00655086]
 [0.00031556 0.00258177 0.00013897 0.00164623 0.00001321 0.9832444
  0.00017223 0.00008944 0.01042663 0.00137154]
 [0.00000301 0.00000005 0.00000129 0.00000085 0.99664223 0.00016097
  0.00003203 0.00004408 0.00032544 0.00278993]
 [0.00005653 0.0041205  0.00598527 0.00047465 0.00260938 0.00446581
  0.9817313  0.0000104  0.00054389 0.0

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/tmpb1op5mth/model.ckpt.
INFO:tensorflow:Loss for final step: 0.07695586.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-06-28-00:01:32
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpb1op5mth/model.ckpt-20000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-06-28-00:01:33
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9683, global_step = 20000, loss = 0.10346629
Printing eval results
{'accuracy': 0.9683, 'loss': 0.10346629, 'global_step': 20000}
